## Imports

In [1]:
# Import necessary libraries and functions

from aux.imports import *
from aux.aux_scraper import scrape_all_pages, fetch_abstract, get_total_pages_from_inspire, add_abstracts
from aux.aux_functions import *

import openai
from openai import OpenAI

import pandas as pd
pd.set_option('display.max_colwidth', None)

from IPython.display import display

import os
import requests
import tarfile

openai.api_key = os.environ["OPENAI_API_KEY"]

# Directory to save the downloaded source files
save_dir = 'my_papers/original_texs'
polished_dir = 'my_papers/polished_texs'

os.makedirs(save_dir, exist_ok=True)
os.makedirs(polished_dir, exist_ok=True)

In [2]:
# Set up Chrome options for headless browsing
chrome_options = Options()
chrome_options.add_argument("--headless")  # Runs Chrome in headless mode

# Initialize the WebDriver with the specified options
driver = webdriver.Chrome(options=chrome_options)

In [3]:
url = "https://inspirehep.net/literature?sort=mostrecent&size=250&page=1&q=a%20muia&ui-citation-summary=true"

In [4]:
df = scrape_all_pages(driver, url)
df.head()

https://inspirehep.net/literature?sort=mostrecent&size=250&q=a%20muia&ui-citation-summary=true


Title  \
0          String Thermodynamics In and Out of Equilibrium: Boltzmann Equations and Random Walks   
1                             Quantum Transitions, Detailed Balance, Black Holes and Nothingness   
2                      Oscillon formation during inflationary preheating with general relativity   
3                                                   Testing BSM physics with gravitational waves   
4  Hunt for light primordial black hole dark matter with ultrahigh-frequency gravitational waves   

                                                    Authors ePrint Number  \
0  A. R. Frey, R. Mahanta, A. Maharana, F. Muia, F. Quevedo    2310.11494   
1             S. Cespedes, S. de Alwis, F. Muia, F. Quevedo    2307.13614   
2                    J. C. Aurrekoetxea, K. Clough, F. Muia    2304.01673   
3               F. Muia, F. Quevedo, A. Schachner, G. Villa    2303.01548   
4                      G. Franciolini, A. Maharana, F. Muia    2205.02153   

  arXiv Category                            DOI  Citation Count  
0         hep-th                           None               1  
1         hep-th                           None               4  
2          gr-qc    10.1103/PhysRevD.108.023501              11  
3         hep-ph  10.1088/1475-7516/2023/09/006               8  
4    astro-ph.CO    10.1103/PhysRevD.106.103520              48

In [5]:
list_of_arxiv_no = df['ePrint Number'].tolist()

In [6]:
for arxiv_id in list_of_arxiv_no:
    url = f'http://arxiv.org/e-print/{arxiv_id}'
    
    # Make the request and download the file
    response = requests.get(url)
    
    if response.status_code == 200:
        tar_path = os.path.join(save_dir, f'{arxiv_id}.tar.gz')
        
        with open(tar_path, 'wb') as file:
            file.write(response.content)
        print(f'Downloaded {arxiv_id}')
        
        # Extract .tex files from the downloaded tar.gz file, if valid
        extract_to = os.path.join(save_dir)  # Specify the directory for extracted files
        os.makedirs(extract_to, exist_ok=True)
        if extract_tex_files(tar_path, extract_to, arxiv_id):
            print(f'Extracted LaTeX sources for {arxiv_id}')
        else:
            print(f'{arxiv_id}.tar.gz is not a valid archive or does not contain .tex files.')
        
        # Optionally, delete the .tar.gz file regardless of extraction success
        os.remove(tar_path)
        print(f'Deleted archive {arxiv_id}.tar.gz')
    else:
        print(f'Failed to download {arxiv_id}. Status code: {response.status_code}')

Downloaded 2310.11494
Extracted LaTeX sources for 2310.11494
Deleted archive 2310.11494.tar.gz
Downloaded 2307.13614
Extracted LaTeX sources for 2307.13614
Deleted archive 2307.13614.tar.gz
Downloaded 2304.01673
Extracted LaTeX sources for 2304.01673
Deleted archive 2304.01673.tar.gz
Downloaded 2303.01548
Extracted LaTeX sources for 2303.01548
Deleted archive 2303.01548.tar.gz
Downloaded 2205.02153
Extracted LaTeX sources for 2205.02153
Deleted archive 2205.02153.tar.gz
Downloaded 2112.11486
Extracted LaTeX sources for 2112.11486
Deleted archive 2112.11486.tar.gz
Downloaded 2112.11650
Extracted LaTeX sources for 2112.11650
Deleted archive 2112.11650.tar.gz
Downloaded 2201.03458
2201.03458.tar.gz is not a valid archive or does not contain .tex files.
Deleted archive 2201.03458.tar.gz
Downloaded 2107.12392
Extracted LaTeX sources for 2107.12392
Deleted archive 2107.12392.tar.gz
Downloaded 2107.03391
Extracted LaTeX sources for 2107.03391
Deleted archive 2107.03391.tar.gz
Downloaded 2103.

In [6]:
newcommand_pattern = re.compile(r'\\newcommand\{\\(\w+)\}\s*\{((?:[^{}]|{[^{}]*})*)\}')

all_matches = []  # This will aggregate all matches from all files

for filename in os.listdir(save_dir):
    if filename.endswith('.tex'):
        #print(filename)
        with open(os.path.join(save_dir, filename), 'r', encoding='utf-8') as file:
            content = file.read()
            matches = newcommand_pattern.findall(content)
            #print(matches)
            all_matches.extend(matches)  # Aggregate matches from this file

replacement_dictionary = {name: replacement for name, replacement in all_matches}


In [7]:
dict_replacem = create_replacement_dictionary(save_dir)

In [20]:
apply_replacement_to_files(save_dir, dict_replacem, polished_dir)

In [23]:
combined_file_path = 'my_papers/combined_latex_file.txt'  # Path for the combined LaTeX file

with open(combined_file_path, 'w', encoding='utf-8') as combined_file:
    first_file = True  # Flag to avoid adding separator before the first file
    for filename in os.listdir(polished_dir):
        if filename.endswith('.tex'):
            file_path = os.path.join(polished_dir, filename)
            with open(file_path, 'r', encoding='utf-8') as file:
                
                content = file.read()
                
                content = re.sub(r'\\begin\{figure(\*?)\}.*?\\end\{figure\1\}', '', content, flags=re.DOTALL)
                print(content[0:1500])

                # Patterns for abstract and section
                abstract_pattern = re.compile(r"\\begin\{abstract\}", re.IGNORECASE)
                section_pattern = re.compile(r"\\section\{")

                # Flag to mark if the abstract or section has been found
                found_abstract_or_section = False
                
                # Remove everything after \begin{thebibliography} if it exists
                content = re.split(r'\\begin\{thebibliography\}', content, maxsplit=1)[0]

                # Remove the acknowledgements section
                content = re.split(r'\\section\*?\{Acknowledgements\}', content, maxsplit=1)[0]

                # Find the first section as a fallback if no abstract is found
                section_start = re.search(r'\\section', content)
                if section_start:
                    content = content[section_start.start():]
                
                # Add separator between papers, except before the first file
                if not first_file:
                    combined_file.write("/------- NEW PAPER -------/\n\n")
                else:
                    first_file = False
                
                combined_file.write(content.strip() + "\n\n")

# Read the combined file
with open(combined_file_path, 'r', encoding='utf-8') as file:
    combined_content = file.read()

\pdfoutput=1
\documentclass[fleqn,usenatbib,useAMS]{mnras}
\usepackage{newtxtext,newtxmath}
\usepackage{amsmath,amssymb}
\usepackage[T1]{fontenc}
%\usepackage{ae,aecompl}
\usepackage{natbib}
\usepackage{epsfig}
\usepackage{graphicx}
\usepackage{tablefootnote}
%\usepackage[export]{adjustbox}
\usepackage{floatrow}
\usepackage{caption}
%\usepackage{hyperref}

\newcommand{}{\mathcal}

\title[Projected bounds on ALPs from ATHENA]{Projected bounds on ALPs from {\it Athena}}
\author[J. P. Conlon et al.]{
Joseph P. Conlon$^{1}$,
Francesca Day$^{1}$, 
Nicholas Jennings$^{1}$\thanks{E-mail: nicholas.jennings@physics.ox.ac.uk}, 
Sven Krippendorf$^{1}$
\newauthor{ and Francesco Muia$^{1}$}
\\
% List of institutions
$^{1}$Rudolf Peierls Centre for Theoretical Physics, 1 Keble Road, Oxford, OX1 3NP, UK\\
}
\date{\today}

\pubyear{2017}

\begin{document}
\label{firstpage}
\pagerange{\pageref{firstpage}--\pageref{lastpage}}
\maketitle

\begin{abstract}
Galaxy clusters represent excellent laboratories 

In [32]:
combined_file_path = 'my_papers/combined_latex_file.txt'  # Path for the combined LaTeX file

# Patterns for abstract, section, acknowledgements, and bibliography
abstract_pattern = re.compile(r"\\(?:begin\{abstract\}|abstract)", re.IGNORECASE)
section_pattern = re.compile(r"\\section\{")
acknowledgements_pattern = re.compile(r"\\(?:section|subsection|subsubsection|paragraph)\*?\s*\{(Acknowledgements|Acknowledgments)\}|\\(?:acknowledgements|acknowledgments)", re.IGNORECASE)
bibliography_pattern = re.compile(r"\\(?:begin\{thebibliography\}|bibliography)")

with open(combined_file_path, 'w', encoding='utf-8') as combined_file:
    first_file = True  # Flag to avoid adding separator before the first file
    for filename in os.listdir(polished_dir):
        if filename.endswith('.tex'):
            file_path = os.path.join(polished_dir, filename)
            with open(file_path, 'r', encoding='utf-8') as file:
                content = file.read()
                
                # Remove figure environments and commented out lines
                content = re.sub(r'\\begin\{figure(\*?)\}.*?\\end\{figure\1\}', '', content, flags=re.DOTALL)
                content = re.sub(r'^%.*\n?', '', content, flags=re.MULTILINE)
                
                # Start parsing at \begin{abstract} or the first \section{...}, if abstract is not present
                start_point = abstract_pattern.search(content) or section_pattern.search(content)
                if start_point:
                    content = content[start_point.start():]
                # Note: if neither \begin{abstract} nor \section is found, content remains unchanged
                
                # Remove everything after \begin{thebibliography}, if present
                content = bibliography_pattern.split(content)[0]

                # Remove the acknowledgements section, if present
                content = acknowledgements_pattern.split(content)[0]

                # Add separator between papers, except before the first file
                if not first_file:
                    combined_file.write(f"\n\n/------- NEW DOCUMENT - {filename} -------/\n\n")
                else:
                    first_file = False
                
                combined_file.write(content.strip() + "\n\n")


# this didn't capture the following cases:

#\section*{Acknowlegdments}
#\paragraph{Acknowledgements}
#\section*{Acknowledgments}
#\acknowledgments

In [10]:
def handle_latex_commands(text, to_remove, to_ignore, to_headline):
    """
    Remove specified LaTeX commands from the text.
    Args:
    - text (str): The input LaTeX document as a string.
    - to_remove (list): A list of commands (as regex patterns) to remove.
    
    Returns:
    - str: The text with specified commands removed.
    """
    for command in to_remove:
        pattern = r'\\' + command + r'(\[[^\]]*\])?(\{[^\}]*\})?\s*'
        text = re.sub(pattern, '', text)
    
    # Handling specific patterns with a more targeted approach
    text = re.sub(r'\\pdfoutput\s*=\s*\d\s*', '', text)
    text = re.sub(r'\\begin\{document\}\s*', '', text)
    text = re.sub(r'\\begin\{titlepage\}\s*', '', text)
    # Add or adjust patterns as needed

    # Handling commands to ignore by retaining their content
    for command in to_ignore:
        if command in ['center', 'array', 'minipage', 'titlepage']:  # Environment commands
            pattern = r'\\begin\{' + command + r'\}(.*?)\\end\{' + command + r'\}'
            text = re.sub(pattern, r'\1', text, flags=re.DOTALL)
        else:  # Text formatting commands
            # Handling the case where commands are used with curly brackets around
            text = re.sub(r'{\\' + command + r'\s+([^}]*)}', r'\1', text)
            # Handling the case where commands are used without curly brackets around
            pattern = r'\\' + command + r'\{([^}]*)\}'
            text = re.sub(pattern, r'\1', text)
            pattern = r'\\' + command + r'(\{([^}]*)\})?'
            text = re.sub(pattern, r'\1', text)        
    
    for command in to_headline:
        # Capitalize the first letter of each command for the output
        formatted_command = command.capitalize()
        # Replace command with formatted headline, including optional arguments
        text = re.sub(r'\\' + command + r'(\[[^\]]*\])?\{([^}]*)\}', r'\n' + formatted_command + r': \2\n', text)
        # Replace command with formatted headline, including optional arguments
        text = re.sub(r'\\begin\{' + command + r'\}(.*?)\\end\{' + command + r'\}', r'\n' + formatted_command + r': \1\n', text, flags=re.DOTALL)

    # Handle citations and footnotes
    text = re.sub(r'\\cite\{([^}]*)\}', r'[\1]', text)
    text = re.sub(r'\\footnote\{([^}]*)\}', r' (\1)', text)

    # Optionally, remove blank lines after processing
    text = re.sub(r'%', '', text)
    # Removing empty curly brackets with only whitespaces
    text = re.sub(r'\{\s*\}', '', text)
    text = re.sub(r'\\{2,}', '', text)
    text = re.sub(r'\n{2,}', ' ', text)
    text = re.sub(r'\s{2,}', ' ', text)


    return text

In [11]:
commands_to_remove = ['usepackage', 'documentclass', 'setcounter', 'numberwithin', 'today', 'pageref', 'thanks', 'pagerange',
                      'setlength', 'definecolor', 'newcommand', 'renewcommand', 'textwidth', 'date', 'text', 'centering',
                      'vskip', 'hskip', 'thispagestyle', 'LARGE', 'Huge', 'huge', 'Large', 'large', 'bibliographystyle', 'bibliography',
                      'normalsize', 'small', 'footnotesize', 'scriptsize', 'tiny', 'label', 'pubyear']

commands_to_ignore = ['textbf', 'mathcal', 'cal' 'textit', 'bf', 'it', 'emph', 'sl', 'sf', 'sc', 'tt', 'center', 'rm',
                      'array', 'minipage', 'titlepage', 'newauthor', 'maketitle', 'quad', 'qquad', 'Bigg', 'mbox']

commands_to_headline = ['section', 'subsection', 'subsubsection', 'paragraph', 'abstract', 'title', 'author', 'keywords', 'appendix']



In [12]:
combined_content[0:1000]

'\\section{Introduction}\n\\label{introduction}\nX-ray astronomy provides a novel arena for fundamental physics. Thanks to exciting recent data, such as the observed excess at 3.5~keV \\cite{Bulbul, Boyarsky}, there has been a renewed interest among particle physicists in the great promise of X-ray astronomy to shed light on physics beyond the Standard Model, including the existence of new particles.\n\nOne area for which X-ray astronomy is particularly suitable\n is in the search for Axion-Like Particles (ALPs).\nALPs are light pseudo-scalars that are a well motivated extension of the Standard Model \\cite{PecceiQuinn,Wilczek,Weinberg} that arise\n generically in string compactifications, for example see \\cite{hep-th/0602233,hep-th/0605206,1206.0819}. A general review of ALPs is \\cite{RingwaldReview}. In the presence of a magnetic field $\\langle B \\rangle$ ALPs and photons interconvert \\cite{Sikivie:1983ip, Raffelt:1987im}, and this induces quasi-sinusoidal oscillations at X-ray 

In [13]:
handle_latex_commands(combined_content, commands_to_remove, commands_to_ignore, commands_to_headline)

'\nSection: Introduction X-ray astronomy provides a novel arena for fundamental physics. Thanks to exciting recent data, such as the observed excess at 3.5~keV [Bulbul, Boyarsky], there has been a renewed interest among particle physicists in the great promise of X-ray astronomy to shed light on physics beyond the Standard Model, including the existence of new particles. One area for which X-ray astronomy is particularly suitable is in the search for Axion-Like Particles (ALPs).\nALPs are light pseudo-scalars that are a well motivated extension of the Standard Model [PecceiQuinn,Wilczek,Weinberg] that arise generically in string compactifications, for example see [hep-th/0602233,hep-th/0605206,1206.0819]. A general review of ALPs is [RingwaldReview]. In the presence of a magnetic field $\\langle B \\rangle$ ALPs and photons interconvert [Sikivie:1983ip, Raffelt:1987im], and this induces quasi-sinusoidal oscillations at X-ray energies in the spectra of sources in and around galaxy clust

In [11]:
# Step 2: Remove figure content, then split the combined file into chunks based on section commands
section_commands = re.compile(r'\\(sub)*section{.*?}', re.DOTALL)

# Read the combined file
with open(combined_file_path, 'r', encoding='utf-8') as file:
    combined_content = file.read()

# Remove content between \begin{figure} and \end{figure}
combined_content = re.sub(r'\\begin\{figure(\*?)\}.*?\\end\{figure\1\}', '', combined_content, flags=re.DOTALL)

# Split the content into chunks
chunks = section_commands.split(combined_content)

# Filter out empty chunks
chunks = [chunk for chunk in chunks if chunk and chunk.strip()]

In [12]:
# Step 3: Store all the chunks into a DataFrame
df_chunks = pd.DataFrame({'chunk': chunks})

print(f"Total chunks created: {len(df_chunks)}")

# Optionally, save the DataFrame to a CSV file
df_chunks.to_csv('latex_chunks.csv', index=False)

Total chunks created: 1155


In [23]:
pd.set_option('display.max_colwidth', None)
display(df_chunks)  # Show the first few chunks for verification

chunk
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

In [13]:
def find_math_expressions(text):
    # Pattern to match LaTeX math environments and inline math
    patterns = [
        r'\$.*?\$',  # Inline math
        r'\\begin\{equation\}.*?\\end\{equation\}',  # Equation environment
        r'\\begin\{eqnarray\}.*?\\end\{eqnarray\}',  # Eqnarray environment
        r'\\begin\{align\}.*?\\end\{align\}',  # Align environment
        # Add more environments as needed
    ]
    combined_pattern = '|'.join(patterns)
    
    # Find all matches and return them
    return [(m.start(), m.end()) for m in re.finditer(combined_pattern, text, flags=re.DOTALL)]

In [14]:
def split_text_preserving_math(text, max_length=3000):
    math_expressions = find_math_expressions(text)
    chunks = []
    current_chunk = ""
    last_index = 0
    
    for start, end in math_expressions:
        # Add text before the math expression to the chunk
        current_chunk += text[last_index:start]
        # Check if current chunk exceeds max length
        if len(current_chunk) > max_length:
            chunks.append(current_chunk)
            current_chunk = ""
        # Add the math expression to the chunk
        current_chunk += text[start:end]
        last_index = end
    
    # Add remaining text after the last math expression
    remaining_text = text[last_index:]
    sentences = re.split(r'(?<=\.)\s', remaining_text)
    for sentence in sentences:
        if len(current_chunk) + len(sentence) > max_length and current_chunk:
            chunks.append(current_chunk)
            current_chunk = ""
        current_chunk += sentence + " "
    
    if current_chunk:
        chunks.append(current_chunk)
        
    return chunks

In [15]:
new_chunks = []
for text in df_chunks['chunk']:
    if len(text) > 3000:
        smaller_chunks = split_text_preserving_math(text)
        new_chunks.extend(smaller_chunks)
    else:
        new_chunks.append(text)

df_new_chunks = pd.DataFrame({'chunk': new_chunks})


In [16]:
df_new_chunks

chunk
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              \pdfoutput=1\n\documentclass[fleqn,usenatbib,useAMS]{mnras}\n\usepackage{newtxtext,newtxmath}\n\usepackage{amsmath,amssymb}\n\usepackage[T1]{fontenc}\n%\usepackage{ae,aecompl}\n\usepackage{natbib}\n\usepackage{epsfig}\n\usepackage{graphicx}\n\usepackage{tablefootnote}\n%\usepackage[export]{adjustbox}\n\usepackage{floatrow}\n\usepackage{caption}\n%\usepackage{hyperref}\n\n\newcommand{}{\mathcal}\n\n\title[Projected bounds on ALPs from ATHENA]{Projected bounds on ALPs from {\it Athena}}\n\author[J. P. Conlon et al.]{\nJoseph P. Conlon$^{1}$,\nFrancesca Day$^{1}$, \nNicholas Jennings$^{1}$\thanks{E-mail: nicholas.jennings@physics.ox.ac.uk}, \nSven Krippendorf$^{1}$\n\newauthor{ and Francesco Muia$^{1}$}\n\\\n% List of institutions\n$^{1}$Rudolf Peierls Centre for Theoretical Physics, 1 Keble Road, Oxford, OX1 3NP, UK\\\n}\n\date{\today}\n\n\pubyear{2017}\n\n\begin{document}\n\label{firstpage}\n\pagerange{\pageref{firstpage}--\pageref{lastpage}}\n\maketitle\n\n\begin{abstract}\nGalaxy clusters represent excellent laboratories to search for Axion-Like Particles (ALPs). They contain magnetic fields which can induce quasi-sinusoidal oscillations in the X-ray spectra of AGNs situated in or behind them. Due to its excellent \nenergy resolution, the X-ray Integral Field Unit (X-IFU) instrument onboard the {\it Athena} X-ray Observatory will be far more sensitive to ALP-induced modulations than current detectors. As a first analysis of the sensitivity of {\it Athena} to the ALP-photon coupling $g_{a \gamma \gamma}$, we simulate observations of the Seyfert galaxy NGC~1275 (hosting the radio source 3C~84) in the Perseus cluster using the SIXTE simulation software. We estimate that for a 200~ks exposure, a non-observation of spectral modulations will constrain ${g_{a\gamma\gamma}\lesssim1.5\times10^{-13}~\rm{GeV}^{-1}}$ for $m_a\lesssim10^{-12}~\rm{eV}$, representing an order of magnitude improvement over constraints derived  using the current generation of satellites.\n\end{abstract}\n\n\begin{keywords}\nastroparticle physics -- elementary particles -- galaxies: clusters: individual: Perseus\n\end{keywords}\n\n
1                                                                                                                                                                                                                                                                  

In [17]:
# Assume df_new_chunks is your DataFrame containing the chunks to translate
chunks_test = df_new_chunks['chunk'].head(10).tolist()  # Take the first 10 chunks for this example

chunk_responses = []

In [21]:
user_prompt_template = """
    Translate the following LaTeX content into plain text, adhering to these rules:
    - Convert \\section, \\subsection, \\abstract, \\chapter, etc., commands into plain text headings like Section, Subsection, Abstract, etc.
    - Keep mathematical equations as in LaTeX, enclosed in $ ... $, \\begin{{equation}} ... \\end{{equation}}, etc.
    - Turn \\begin{{itemize}} ... \\end{{itemize}}, \\begin{{enumerate}} ... \\end{{enumerate}} into bullet/numbered lists.
    - Enclose citations like \\cite{{cited_paper}} in square brackets: [cited_paper].
    - Remove all LaTeX commands that do not add information to the plain text.
    - If a chunk does not return meaningful plain text or equations, keep the output empty.

    LaTeX content to translate:
    {{chunk}}
"""

In [29]:
# Assuming `chunks_test` is your list of LaTeX chunks
for chunk in chunks_test:
    # Constructing messages as a list of dictionaries
    messages = [
        {"role": "system", "content": user_prompt_template},
        {"role": "user", "content": chunk}
    ]
    
    try:
        response = client.chat.completions.create(
            model="gpt-3.5-turbo-0125",
            messages=messages
            #temperature=0.5,
            #max_tokens=1024
        )

        # Correctly accessing the translated text from the response
        translated_text = response.choices[-1].message.content if response.choices else "No response"

        # Appending the LaTeX chunk and its translated text to the list
        chunk_responses.append({
            "LaTeX Code": chunk,
            "Translated Text": translated_text
        })
    except Exception as e:
        print(f"An error occurred: {e}")
        chunk_responses.append({
            "LaTeX Code": chunk,
            "Translated Text": "Error processing this chunk"
        })


In [34]:
chunk_responses

[{'LaTeX Code': '\\pdfoutput=1\n\\documentclass[fleqn,usenatbib,useAMS]{mnras}\n\\usepackage{newtxtext,newtxmath}\n\\usepackage{amsmath,amssymb}\n\\usepackage[T1]{fontenc}\n%\\usepackage{ae,aecompl}\n\\usepackage{natbib}\n\\usepackage{epsfig}\n\\usepackage{graphicx}\n\\usepackage{tablefootnote}\n%\\usepackage[export]{adjustbox}\n\\usepackage{floatrow}\n\\usepackage{caption}\n%\\usepackage{hyperref}\n\n\\newcommand{}{\\mathcal}\n\n\\title[Projected bounds on ALPs from ATHENA]{Projected bounds on ALPs from {\\it Athena}}\n\\author[J. P. Conlon et al.]{\nJoseph P. Conlon$^{1}$,\nFrancesca Day$^{1}$, \nNicholas Jennings$^{1}$\\thanks{E-mail: nicholas.jennings@physics.ox.ac.uk}, \nSven Krippendorf$^{1}$\n\\newauthor{ and Francesco Muia$^{1}$}\n\\\\\n% List of institutions\n$^{1}$Rudolf Peierls Centre for Theoretical Physics, 1 Keble Road, Oxford, OX1 3NP, UK\\\\\n}\n\\date{\\today}\n\n\\pubyear{2017}\n\n\\begin{document}\n\\label{firstpage}\n\\pagerange{\\pageref{firstpage}--\\pageref{lastp

In [33]:
# Creating a DataFrame from the responses
df_translations = pd.DataFrame(chunk_responses)
display(df_translations)

LaTeX Code  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            \pdfoutput=1\n\documentclass[fleqn,usenatbib,useAMS]{mnras}\n\usepackage{newtxtext,newtxmath}\n\usepackage{amsmath,amssymb}\n\usepackage[T1]{fontenc}\n%\usepackage{ae,aecompl}\n\usepackage{natbib}\n\usepackage{epsfig}\n\usepackage{graphicx}\n\usepackage{tablefootnote}\n%\usepackage[export]{adjustbox}\n\usepackage{floatrow}\n\usepackage{caption}\n%\usepackage{hyperref}\n\n\newcommand{}{\mathcal}\n\n\title[Projected bounds on ALPs from ATHENA]{Projected bounds on ALPs from {\it Athena}}\n\author[J. P. Conlon et al.]{\nJoseph P. Conlon$^{1}$,\nFrancesca Day$^{1}$, \nNicholas Jennings$^{1}$\thanks{E-mail: nicholas.jennings@physics.ox.ac.uk}, \nSven Krippendorf$^{1}$\n\newauthor{ and Francesco Muia$^{1}$}\n\\\n% List of institutions\n$^{1}$Rudolf Peierls Centre for Theoretical Physics, 1 Keble Road, Oxford, OX1 3NP, UK\\\n}\n\date{\today}\n\n\pubyear{2017}\n\n\begin{document}\n\label{firstpage}\n\pagerange{\pageref{firstpage}--\pageref{lastpage}}\n\maketitle\n\n\begin{abstract}\nGalaxy clusters represent excellent laboratories to search for Axion-Like Particles (ALPs). They contain magnetic fields which can induce quasi-sinusoidal oscillations in the X-ray spectra of AGNs situated in or behind them. Due to its excellent \nenergy resolution, the X-ray Integral Field Unit (X-IFU) instrument onboard the {\it Athena} X-ray Observatory will be far more sensitive to ALP-induced modulations than current detectors. As a first analysis of the sensitivity of {\it Athena} to the ALP-photon coupling $g_{a \gamma \gamma}$, we simulate observations of the Seyfert galaxy NGC~1275 (hosting the radio source 3C~84) in the Perseus cluster using the SIXTE simulation software. We estimate that for a 200~ks exposure, a non-observation of spectral modulations will constrain ${g_{a\gamma\gamma}\lesssim1.5\times10^{-13}~\rm{GeV}^{-1}}$ for $m_a\lesssim10^{-12}~\rm{eV}$, representing an order of magnitude improvement over constraints derived  using the current generation of satellites.\n\end{abstract}\n\n\begin{keywords}\nastroparticle physics -- elementary particles -- galaxies: clusters: individual: Perseus\n\end{keywords}\n\n   
1                                                                                                                                                                                                                                                         

### Upload file

In [139]:
#name_file = "1903.06239/Review.tex" # Palti's review
#name_file = "2008.10625/ls.tex" # Hebecker's review
#name_file = "2303.04819/Sections/Introduction.tex" # StringCosmo review. The sections are: Introduction, CosmoOverview, Moduli, Inflation, Postinflation, DarkEnergy, Alternatives, Outlook
#name_file = "2310.20559/ls.tex" # McAllister-Quevedo's review
name_file = "0701050/review.tex" # Denef-Douglas-Kachru's review

latex_file_path = 'Files/' + name_file

# Extract the LaTeX content
latex_content = extract_latex_content(latex_file_path, "\\startdocument", "\\enddocument")

len(latex_content)

76800

### Simplify the latex text using common replacements

In [140]:
replacements = {
        r'\\d': 'd',
        r'\\G': 'G',
        r'\\O': 'O',
        r'\\C': 'C',
        r'\\V': 'V',
        r'\\L': 'L',
        r'\\R': 'R',
        r'\\S': 'S',
        r'\\Mp': 'Mp',
        r'\\cN': 'N',
        r'\\cC': 'C',
        r'\\cP': 'P',
        r'\\cR': 'R',
        r'\\vo': 'V',
        r'\\Kahler': 'Kahler',
        r'\\flux': 'flux',
        r'\\KK': 'Kaluza-Klein',
        r'\\n': ' '
    }                                        # This can be improved adding more replacements

brace_commands = [r'\\emph', r'\\footnote', r'\\it', r'\\em', r'\\ref', r'\\eqref']               # This can be improved adding more replacements

simplified_text = replace_latex_commands(latex_content, replacements, brace_commands)
len(simplified_text)

76552

### Polish latex text removing standard latex commands

In [141]:
polished_text = clean_latex_content(simplified_text)         # This can be improved adding more commands
len(polished_text)

75561

### Split the text in chunks

In [143]:
no_char_in_chunk = 2000

chunks = chunk_text(polished_text, no_char_in_chunk)
chunks = [chunk.replace("%", "") for chunk in chunks]
print("The number of chunks is: " + str(len(chunks)) + ".")
chunks[23:25]

The number of chunks is: 45.


["The number of vacua $\\phi_*$ in an interval $I$ is given by \\begin{equation}\n\\label{ansatz}\nds^2 = g_{\\mu u} dx^{\\mu}dx^{ u} + R^2 \\tilde g_{mn}dy^m dy^n\n\\end{equation}6 where $\\theta(x):=1$ if $x>0$, $\\theta(x):=0$ if $x<0$. The integrand $delta(V') |V''|$ gives a contribution $+1$ for each critical point in $I$, while $\\theta(V'')$ restricts to actual minima. Now in the large $L$ limit, we can approximate the sum over $(N,M)$ by an integral, and write \\begin{equation}\n\\label{ansatz}\nds^2 = g_{\\mu u} dx^{\\mu}dx^{ u} + R^2 \\tilde g_{mn}dy^m dy^n\n\\end{equation}7 where $\\rho(\\phi)$ can be interpreted as a vacuum number density on moduli space. To evaluate the integral over $(N,M)$ at a given fixed $\\phi$, it is convenient to make the following linear change of variables $(N,M) \\to (v',v'')$: \\begin{equation}\n\\label{ansatz}\nds^2 = g_{\\mu u} dx^{\\mu}dx^{ u} + R^2 \\tilde g_{mn}dy^m dy^n\n\\end{equation}8 This change of variables has Jacobian $=1$, and the 

### Define the prompt to create the Q&A using the text from the papers

In [144]:
# Define the number of Q&A pairs you want to generate for each chunk
num_questions = 3

In [145]:
system_prompt_template = "You are an expert in theoretical physics. I will provide a text, and I'd like you to generate {num_questions} questions a researcher-level colleague might ask about the topic of the text. Then, provide detailed answers to these questions as an expeert in the field. Format your responses as follows: 'Question 1: [question here] Answer 1: [answer here]' and so on for all {num_questions} questions."

user_prompt_template = "Based on the following text, please generate the questions and answers as instructed. Text: {chunk}"

display(system_prompt_template)
display(user_prompt_template)


"You are an expert in theoretical physics. I will provide a text, and I'd like you to generate {num_questions} questions a researcher-level colleague might ask about the topic of the text. Then, provide detailed answers to these questions as an expeert in the field. Format your responses as follows: 'Question 1: [question here] Answer 1: [answer here]' and so on for all {num_questions} questions."

'Based on the following text, please generate the questions and answers as instructed. Text: {chunk}'

### Generate the Q&A using chat-gpt 3.5 turbo

In [146]:
client = OpenAI()

# Initialize a list to store chunk and response pairs
chunk_responses = []

# Assume chunks_test is a list of text chunks you want to generate Q&A for
for chunk in chunks:
    system_prompt, user_prompt = generate_prompt(chunk, num_questions, system_prompt_template, user_prompt_template)
    
    # Call the OpenAI API once per chunk
    response = client.chat.completions.create(
        model="gpt-3.5-turbo-0125",
        messages=[system_prompt, user_prompt]
    )
    
    # Append both the chunk and its response to the chunk_responses list
    chunk_responses.append({
        "chunk": chunk,
        "response": response.choices[-1].message.content if response.choices else "No response"
    })


In [147]:
# Initialize lists to hold the DataFrame data
chunk_list = []
question_list = []
answer_list = []
sub_index = []

# Process each chunk-response pair
for item in chunk_responses:
    chunk = item['chunk']
    response = item['response']
    
    # Split the response into Q&As
    qas = response.split('\n\n')  # Assuming two newlines separate each Q&A pair
    for i, qa in enumerate(qas):
        # Attempt to split the QA into question and answer
        parts = qa.split('\nAnswer ')
        if len(parts) == 2:
            question = parts[0].replace('Question {}: '.format(i+1), '').strip()
            answer = parts[1].strip()
            chunk_list.append(chunk)
            question_list.append(question)
            answer_list.append(answer)
            sub_index.append(i+1)

In [160]:
# Create a MultiIndex from the chunks and their corresponding sub_index
multi_index = pd.MultiIndex.from_arrays([chunk_list, sub_index], names=['Chunk', 'Q&A Index'])
answer_list = [re.sub(r'^\d+: ', '', answer) for answer in answer_list]

# Construct the DataFrame
df_multi = pd.DataFrame({'Question': question_list, 'Answer': answer_list}, index=multi_index)

# Display the DataFrame
#df_multi

### Visualize the Q&A ina  dataframe

In [149]:
qa_df = pd.DataFrame({
    'Question': question_list,
    'Answer': answer_list
})

qa_df = qa_df
qa_df

Question  \
0   How did the second superstring revolution of 1994-97 address the doubts surrounding string theory being defined only as a perturbative expansion and the need for non-perturbative physics in constructing a completely realistic model?   
1                                                                                      What were some of the key discoveries that led particle physicists to consider superstring theory as a viable contender for a "theory of everything"?   
2                               How did the concept of duality play a significant role in the development and acceptance of string/M theory as a unified framework encompassing various string theories and eleven-dimensional supergravity?   
3                                                                                                                                            What is the central idea of duality in the context of string/M theory as mentioned in the text?   
4                                                                                                                       How did the "second superstring revolution" from 1994-97 contribute to theoretical physics as mentioned in the text?   
..                                                                                                                                                                                                                                       ...   
94                                                                                                           How does the text relate the search for inflationary measures in theoretical physics to analogous problems in particle physics?   
95                                                       In the context of the text, what role do asymptotically free gauge theories coupled to gravity play in advancing theoretical physics and potentially leading to the Standard Model?   
96                                                       What challenges are encountered when considering different field theories that might lead to similar low energy physics, and how can researchers navigate through this uncertainty?   
97                                                   What experimental approaches could be used to test proposals arising from field theories, particularly those related to subtle corrections and higher-energy phenomena in astrophysics?   
98                                                                 How might exotic physics, particularly related to string theory, be observed and what role does early cosmology play in potentially providing evidence for string theory?   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           Answer  
0                                                                                                                                                                         The second superstring revolution of 1994-97 addressed these doubts by convincingly arguing that all the different string theories and eleven-dimensional supergravity are actually limits or aspects of a unified framework called string/M theory. The central idea of duality emerged, demonstrating that the strong coupling limit of one string theory can be equivalent to another weakly coupled theory, leading to a more unified understanding of the subject.  
1                                                                                          

### Save the dataframe in a csv and parquet format

In [152]:
qa_df.to_csv("Datasets/0701050.csv")
qa_df.to_parquet("Datasets/0701050.parquet")

### Upload csv datasets for further processing

In [153]:
df_test = pd.read_csv("Datasets/0701050.csv", index_col=0)
df_test

Question  \
0   How did the second superstring revolution of 1994-97 address the doubts surrounding string theory being defined only as a perturbative expansion and the need for non-perturbative physics in constructing a completely realistic model?   
1                                                                                      What were some of the key discoveries that led particle physicists to consider superstring theory as a viable contender for a "theory of everything"?   
2                               How did the concept of duality play a significant role in the development and acceptance of string/M theory as a unified framework encompassing various string theories and eleven-dimensional supergravity?   
3                                                                                                                                            What is the central idea of duality in the context of string/M theory as mentioned in the text?   
4                                                                                                                       How did the "second superstring revolution" from 1994-97 contribute to theoretical physics as mentioned in the text?   
..                                                                                                                                                                                                                                       ...   
94                                                                                                           How does the text relate the search for inflationary measures in theoretical physics to analogous problems in particle physics?   
95                                                       In the context of the text, what role do asymptotically free gauge theories coupled to gravity play in advancing theoretical physics and potentially leading to the Standard Model?   
96                                                       What challenges are encountered when considering different field theories that might lead to similar low energy physics, and how can researchers navigate through this uncertainty?   
97                                                   What experimental approaches could be used to test proposals arising from field theories, particularly those related to subtle corrections and higher-energy phenomena in astrophysics?   
98                                                                 How might exotic physics, particularly related to string theory, be observed and what role does early cosmology play in potentially providing evidence for string theory?   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           Answer  
0                                                                                                                                                                         The second superstring revolution of 1994-97 addressed these doubts by convincingly arguing that all the different string theories and eleven-dimensional supergravity are actually limits or aspects of a unified framework called string/M theory. The central idea of duality emerged, demonstrating that the strong coupling limit of one string theory can be equivalent to another weakly coupled theory, leading to a more unified understanding of the subject.  
1                                                                                          

### Concatenate all datasets from various papers to create a single dataset about string phenomenology (and save it)

In [161]:
from sklearn.utils import shuffle

directory_path = 'Datasets/'

# Initialize a list to hold the dataframes
dataframes = []

# Iterate through all files in the directory
for filename in os.listdir(directory_path):
    if filename.endswith('.csv'):
        # Load each CSV file into a DataFrame, excluding the index
        df_temp = pd.read_csv(os.path.join(directory_path, filename), index_col=0)
        # Append the DataFrame to the list
        dataframes.append(df_temp)

# Concatenate all the DataFrames into a single DataFrame
concatenated_df = pd.concat(dataframes, ignore_index=True)

# Shuffle the rows of the concatenated DataFrame
shuffled_df = shuffle(concatenated_df)

# Reset the index to get rid of the old indexing
shuffled_df.reset_index(drop=True, inplace=True)

shuffled_df

Question  \
0                                                                                 Can dS vacua be obtained in the IIB setting, and what are the methods or approaches suggested to achieve this?   
1            What role do the slow-roll conditions play in multi-field inflation, and how do they relate to the decomposition of the inflationary trajectory into tangent and normal directions?   
2                            How does the distribution of flux values in the model impact the number of solutions, and how does the choice of parameters affect the range of possible solutions?   
3                          How does the inclusion of Kaluza-Klein (KK) modes within the $R^d$-dimensional theory relate to the universal quantum gravity bound and the effective theory's scale?   
4                                                       What are some of the key criticisms or challenges faced by the swampland approach and the Planckian censorship conjecture in particular?   
...                                                                                                                                                                                          ...   
5197                                                                                What are bifurcated throats and how do they address backreaction effects in the model mentioned in the text?   
5198  In the context of string inflationary scenarios, what distinguishes the classes of models focused on in the text from the broader set of string-inspired models present in the literature?   
5199                                                           What is the significance of the DBI inflation scenario and its non-canonical kinetic terms in the context of theoretical physics?   
5200                                                      What is the significance of the equation of state of dark energy changing with time, and how does it relate to inflationary cosmology?   
5201                                              How do the Polchinski equation and the Wetterich equation relate to the RG evolution and the effective average action in quantum field theory?   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 Answer  
0                                                                                                                                                                                                        Yes, it is possible to obtain de Sitter (dS) vacua in the IIB setting by incorporating additional effects from the low energy effective action or by adopting a more generalized approach to seeking minima of the effective action. Various proposals have been put forward to construct dS vacua. These proposals can be found in recent research that summarizes the state of the art in dS constructions and highlights the challenges involved. Additional strategies include incorporating anti-branes, which were originally proposed as part of the KKLT construction.  
1                                                                                                                                                                                                                                                                                  In multi-field inflation, the sl

In [159]:
shuffled_df.to_csv("Datasets/StringPhenoDataset.csv")
shuffled_df.to_parquet("Datasets/StringPhenoDataset.parquet")